In [1]:
#Imports

from marketsai.markets.diff_demand import DiffDemandDiscrete

#import ray

from ray import tune, shutdown, init
from ray.tune.registry import register_env
from ray.rllib.agents.a3c.a2c import A2CTrainer
from ray.rllib.agents.dqn.dqn import DQNTrainer
from ray.tune.integration.mlflow import MLflowLoggerCallback
from ray.rllib.utils.schedules.exponential_schedule import ExponentialSchedule

import random
import math
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import logging

/Users/matiascovarrubias/Library/Caches/pypoetry/virtualenvs/marketsai-reVLCGV_-py3.8/lib/python3.8/site-packages/pandas/compat/__init__.py:97: UserWarning: Could not import the lzma module. Your installed Python is incomplete. Attempting to use lzma compression will result in a RuntimeError.
  warnings.warn(msg)
Instructions for updating:
non-resource variables are not supported in the long term


In [2]:
# STEP 0: Inititialize ray

NUM_CPUS = 14
shutdown()
init(num_cpus=NUM_CPUS, 
    logging_level=logging.ERROR,
)


2021-04-05 15:25:32,712	INFO services.py:1172 -- View the Ray dashboard at http://127.0.0.1:8265


{'node_ip_address': '192.168.1.202',
 'raylet_ip_address': '192.168.1.202',
 'redis_address': '192.168.1.202:12138',
 'object_store_address': '/tmp/ray/session_2021-04-05_15-25-31_879412_32733/sockets/plasma_store',
 'raylet_socket_name': '/tmp/ray/session_2021-04-05_15-25-31_879412_32733/sockets/raylet',
 'webui_url': '127.0.0.1:8265',
 'session_dir': '/tmp/ray/session_2021-04-05_15-25-31_879412_32733',
 'metrics_export_port': 56911,
 'node_id': '1753081ab19388f8798af0ee0968bda7839172d9ce9a38cc6c018ff2'}

In [3]:
# STEP 1: register environment

register_env("diffdemanddiscrete", DiffDemandDiscrete)
env = DiffDemandDiscrete()
policy_ids = ["policy_{}".format(i) for i in range(env.n_agents)]

In [6]:
# STEP 2: Experiment configuration

MAX_STEPS = 2000 * 1000
PRICE_BAND_WIDE = 0.1
LOWER_PRICE = 1.47 - PRICE_BAND_WIDE
HIGHER_PRICE = 1.93 + PRICE_BAND_WIDE
DEC_RATE = math.e ** (-4 * 10 ** (-6))
DEC_RATE_HIGH = math.e ** (-4 * 10 ** (-6) * 4)

env_config = {
    "lower_price": [LOWER_PRICE for i in range(env.n_agents)],
    "higher_price": [HIGHER_PRICE for i in range(env.n_agents)],
}
exploration_config = {
    "type": "EpsilonGreedy",
    "epsilon_schedule": ExponentialSchedule(
        schedule_timesteps=1,
        framework=None,
        initial_p=1,
        decay_rate=DEC_RATE,
    ),
}

config = {
    "gamma": 0.95,
    "lr": 0.15,
    "env": "diffdemanddiscrete",
    "exploration_config": exploration_config,
    "env_config": env_config,
    "horizon": 100,
    "soft_horizon": True,
    "no_done_at_end": True,
    "multiagent": {
        "policies": {
            policy_ids[i]: (
                None,
                env.observation_space["agent_{}".format(i)],
                env.action_space["agent_{}".format(i)],
                {},
            )
            for i in range(env.n_agents)
        },
        "policy_mapping_fn": (lambda agent_id: policy_ids[int(agent_id.split("_")[1])]),
    },
    "framework": "torch",
    "num_workers": NUM_CPUS - 1,
    "num_gpus": 0,
}

stop = {"info/num_steps_trained": MAX_STEPS}

In [7]:
#Step 3: Experiments

exp_name = "DQN_base_April4"
results = tune.run(
    "DQN",
    name=exp_name,
    config=config,
    checkpoint_freq=250,
    checkpoint_at_end=True,
    stop=stop,
    #metric="episode_reward_mean",
    #mode="max",
    callbacks=[MLflowLoggerCallback(experiment_name=exp_name, save_artifact=True)],
)

#best_checkpoint = results.best_checkpoint
#print("Best checkpont:", best_checkpoint)

/Library/Caches/pypoetry/virtualenvs/marketsai-reVLCGV_-py3.8/lib/python3.8/site-packages/pandas/compat/__init__.py:97: UserWarning: Could not import the lzma module. Your installed Python is incomplete. Attempting to use lzma compression will result in a RuntimeError.
(pid=50851)   warnings.warn(msg)
(pid=50831) WARNING:tensorflow:From /Users/matiascovarrubias/Library/Caches/pypoetry/virtualenvs/marketsai-reVLCGV_-py3.8/lib/python3.8/site-packages/tensorflow/python/compat/v2_compat.py:96: disable_resource_variables (from tensorflow.python.ops.variable_scope) is deprecated and will be removed in a future version.
(pid=50831) Instructions for updating:
(pid=50831) non-resource variables are not supported in the long term
(pid=50833) WARNING:tensorflow:From /Users/matiascovarrubias/Library/Caches/pypoetry/virtualenvs/marketsai-reVLCGV_-py3.8/lib/python3.8/site-packages/tensorflow/python/compat/v2_compat.py:96: disable_resource_variables (from tensorflow.python.ops.variable_scope) is depr

Result for DQN_diffdemanddiscrete_46daa_00000:
  custom_metrics: {}
  date: 2021-04-05_15-29-58
  done: false
  episode_len_mean: 100.0
  episode_reward_max: 37.68791468558199
  episode_reward_mean: 33.466969079365406
  episode_reward_min: 27.595777035567995
  episodes_this_iter: 0
  episodes_total: 52
  experiment_id: d25e1ace110d476ea8c85738b18067d1
  hostname: Matiass-MBP.fios-router.home
  info:
    last_target_update_ts: 6240
    learner:
      policy_0:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 0.0035122008994221687
        max_q: 4.49836540222168
        mean_q: 4.39535665512085
        mean_td_error: -0.03446757793426514
        min_q: 4.260335922241211
      policy_1:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 0.010347233153879642
        max_q: 4.725582122802734
        mean_q: 4.614843368530273
        mean_td_error: 0.09726646542549133
        min_q: 4.527268886566162
    num_steps_sampled: 6240
    num_steps_traine

Result for DQN_diffdemanddiscrete_46daa_00000:
  custom_metrics: {}
  date: 2021-04-05_15-30-03
  done: false
  episode_len_mean: 100.0
  episode_reward_max: 38.028927930780306
  episode_reward_mean: 33.8527760559795
  episode_reward_min: 27.595777035567995
  episodes_this_iter: 0
  episodes_total: 104
  experiment_id: d25e1ace110d476ea8c85738b18067d1
  hostname: Matiass-MBP.fios-router.home
  info:
    last_target_update_ts: 11440
    learner:
      policy_0:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 0.0020167354959994555
        max_q: 4.751718521118164
        mean_q: 4.654812335968018
        mean_td_error: 0.005046293139457703
        min_q: 4.47811222076416
      policy_1:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 0.005699516274034977
        max_q: 4.978097438812256
        mean_q: 4.878890514373779
        mean_td_error: 0.06420794129371643
        min_q: 4.700623512268066
    num_steps_sampled: 11440
    num_steps_tra

Result for DQN_diffdemanddiscrete_46daa_00000:
  custom_metrics: {}
  date: 2021-04-05_15-30-08
  done: false
  episode_len_mean: 100.0
  episode_reward_max: 38.45018280954326
  episode_reward_mean: 34.14610152615141
  episode_reward_min: 29.191008739108998
  episodes_this_iter: 0
  episodes_total: 156
  experiment_id: d25e1ace110d476ea8c85738b18067d1
  hostname: Matiass-MBP.fios-router.home
  info:
    last_target_update_ts: 16640
    learner:
      policy_0:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 0.0027820125687867403
        max_q: 4.829563140869141
        mean_q: 4.736533164978027
        mean_td_error: 0.03750382363796234
        min_q: 4.566542625427246
      policy_1:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 0.003596836468204856
        max_q: 5.077118873596191
        mean_q: 4.998673915863037
        mean_td_error: 0.04728759825229645
        min_q: 4.835931777954102
    num_steps_sampled: 16640
    num_steps_tra

Result for DQN_diffdemanddiscrete_46daa_00000:
  custom_metrics: {}
  date: 2021-04-05_15-30-14
  done: false
  episode_len_mean: 100.0
  episode_reward_max: 38.363682440116605
  episode_reward_mean: 34.04989710096292
  episode_reward_min: 29.2137297854637
  episodes_this_iter: 0
  episodes_total: 208
  experiment_id: d25e1ace110d476ea8c85738b18067d1
  hostname: Matiass-MBP.fios-router.home
  info:
    last_target_update_ts: 21840
    learner:
      policy_0:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 0.002318268408998847
        max_q: 4.949349880218506
        mean_q: 4.814689636230469
        mean_td_error: 0.021491825580596924
        min_q: 4.700092315673828
      policy_1:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 0.004607425071299076
        max_q: 5.296866416931152
        mean_q: 5.157344818115234
        mean_td_error: 0.07520937919616699
        min_q: 4.959648609161377
    num_steps_sampled: 21840
    num_steps_trai

...

Result for DQN_diffdemanddiscrete_46daa_00000:
  custom_metrics: {}
  date: 2021-04-05_17-41-29
  done: false
  episode_len_mean: 100.0
  episode_reward_max: 56.341937284682345
  episode_reward_mean: 52.25795938489357
  episode_reward_min: 47.870265815549786
  episodes_this_iter: 13
  episodes_total: 32448
  experiment_id: d25e1ace110d476ea8c85738b18067d1
  hostname: Matiass-MBP.fios-router.home
  info:
    last_target_update_ts: 3244800
    learner:
      policy_0:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 0.0016137645579874516
        max_q: 5.227182865142822
        mean_q: 5.182714462280273
        mean_td_error: 0.033558234572410583
        min_q: 5.097163200378418
      policy_1:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 0.0026039262302219868
        max_q: 5.3868889808654785
        mean_q: 5.360749244689941
        mean_td_error: 0.04288136959075928
        min_q: 5.210402965545654
    num_steps_sampled: 3244800
    nu

Result for DQN_diffdemanddiscrete_46daa_00000:
  custom_metrics: {}
  date: 2021-04-05_17-41-35
  done: false
  episode_len_mean: 100.0
  episode_reward_max: 56.341937284682345
  episode_reward_mean: 52.2307747245244
  episode_reward_min: 47.870265815549786
  episodes_this_iter: 13
  episodes_total: 32461
  experiment_id: d25e1ace110d476ea8c85738b18067d1
  hostname: Matiass-MBP.fios-router.home
  info:
    last_target_update_ts: 3246880
    learner:
      policy_0:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 0.0007109682774171233
        max_q: 5.2270002365112305
        mean_q: 5.190212726593018
        mean_td_error: -0.003986716270446777
        min_q: 5.106388568878174
      policy_1:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 0.00415044603869319
        max_q: 5.45855712890625
        mean_q: 5.424983501434326
        mean_td_error: 0.06839108467102051
        min_q: 5.303229808807373
    num_steps_sampled: 3246880
    num_s

Result for DQN_diffdemanddiscrete_46daa_00000:
  custom_metrics: {}
  date: 2021-04-05_17-41-42
  done: false
  episode_len_mean: 100.0
  episode_reward_max: 54.54160669573268
  episode_reward_mean: 48.762843600676604
  episode_reward_min: 39.1920823901872
  episodes_this_iter: 13
  episodes_total: 32500
  experiment_id: d25e1ace110d476ea8c85738b18067d1
  hostname: Matiass-MBP.fios-router.home
  info:
    last_target_update_ts: 3250000
    learner:
      policy_0:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 0.012239383533596992
        max_q: 5.109202861785889
        mean_q: 4.870032787322998
        mean_td_error: -0.16118782758712769
        min_q: 4.812065601348877
      policy_1:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 0.0005619118455797434
        max_q: 5.340948104858398
        mean_q: 5.292760848999023
        mean_td_error: 0.0013549476861953735
        min_q: 5.194937229156494
    num_steps_sampled: 3250000
    num_

Result for DQN_diffdemanddiscrete_46daa_00000:
  custom_metrics: {}
  date: 2021-04-05_17-41-44
  done: true
  episode_len_mean: 100.0
  episode_reward_max: 54.54160669573268
  episode_reward_mean: 48.762843600676625
  episode_reward_min: 39.1920823901872
  episodes_this_iter: 0
  episodes_total: 32500
  experiment_id: d25e1ace110d476ea8c85738b18067d1
  hostname: Matiass-MBP.fios-router.home
  info:
    last_target_update_ts: 3251040
    learner:
      policy_0:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 0.008442028425633907
        max_q: 5.105372428894043
        mean_q: 4.898809909820557
        mean_td_error: 0.10591916739940643
        min_q: 4.746625900268555
      policy_1:
        allreduce_latency: 0.0
        cur_lr: 0.15
        grad_gnorm: 0.0006780619733035564
        max_q: 5.330031394958496
        mean_q: 5.292232036590576
        mean_td_error: -0.0040139853954315186
        min_q: 5.219736099243164
    num_steps_sampled: 3251040
    num_st

2021-04-05 17:41:45,735	INFO tune.py:450 -- Total run time: 7920.68 seconds (7920.52 seconds for the tuning loop).


In [ ]:
#Step 4: Evaluation

config["evaluation_config"] = {"explore": False}
trained_trainer = DQNTrainer(config=config)
trained_trainer.restore(best_checkpoint)
price_agent0_list = []
reward_agent0_list = []
price_agent1_list = []
reward_agent1_list = []
obs, reward, done, info = env.step({"agent_0": 1, "agent_1": 11})
for i in range(500):

    action_agent0 = trained_trainer.compute_action(obs["agent_0"], policy_id="policy_0")
    action_agent1 = trained_trainer.compute_action(obs["agent_1"], policy_id="policy_1")
    obs, reward, done, info = env.step(
        {"agent_0": action_agent0, "agent_1": action_agent1}
    )
    price_agent0_list.append(info["agent_0"])
    reward_agent0_list.append(reward["agent_0"])
    price_agent1_list.append(info["agent_1"])
    reward_agent1_list.append(reward["agent_1"])

plt.ion()

plt.plot(price_agent0_list)
plt.show()
plt.plot(price_agent1_list)
plt.show()

IRresults = {
    "Profits Agent 0": reward_agent0_list,
    "Profits Agent 1": reward_agent1_list,
    "Price Agent 0": price_agent0_list,
    "Price Agent 1": price_agent1_list,
}
df_IR = pd.DataFrame(IRresults)
df_IR.to_csv("collusion_IR_DQN.csv")